# TP 10-3 : Tests Statistiques

Le but du TP est de mettre en oeuvre le test statistique de t-student dans un contexte de régression.


| Numéro        | Compétence           | 
|:------------- |:--------------------:|
|TS004|	Être capable de déterminer la statistique à utiliser|
|TS005|	Savoir conclure suite à un résultat du test statistique|
|TS201|	Savoir dans quel contexte utiliser un test de student|
|TS202|	Connaître les limites du test de student|
|TS203|	Savoir calculer le nombre de degrés de liberté d’un test de student|
|PY603|	Être capable de mettre en œuvre un test de student|


# Test de Student et Hauteurs d'Arbres

Dans deux types de forêts distincts, on a mesuré en mètre les hauteurs dominantes respectivement de 14 et 13 peuplements du même age choisis au hasard et indépendamment.


type\peuplement   | 1|2|3|4|5|6|7|8|9|10|11|12|13|14|
---|---|---|---|---|---|---|---|---|---|---|---|---|---|---
type 1 |23.4 |24.4 |24.6 |24.9 |25.0 |26.2 |26.3 |26.8 |26.8 |26.9 |27.0 |27.6 |27.7 |28.5
type 2 |22.5 |22.9 |23.7 |24.0 |24.4 |24.5 |25.3 |26.0 |26.2 |26.4 |26.7 |26.9 |27.4| |

Considérons un risque de première espèce de 0,05. En considérant que la variance des hauteurs mesurées est connue $(\sigma^2 = 1.7)$, on cherche à savoir si les hauteurs moyennes des deux types de forêts sont identiques.


1. Posez les hypothèses

* $H_0$   les deux forêts sont identiques : $\mu_1 = \mu_2$    
* $H_1$    les deux forêts sont différentes: $\mu_1 \neq \mu_2$

2. Quel statistique et quel test allez vous utilisez ? Justifiez votre réponse !


la différence des moyennes centrée réduite/ test z car variance connue et H_0 suit une loi normale.

3. Calculez la statistique et la p-valeur associées à vos données

In [7]:
import numpy as np
import scipy.stats as stats
x = np.array([23.4, 24.4, 24.6, 24.9, 25.0, 26.2, 26.3, 26.8, 26.8, 26.9, 27.0, 27.6, 27.7, 28.5])
y = np.array([22.5, 22.9, 23.7, 24.0, 24.4, 24.5, 25.3, 26.0, 26.2, 26.4, 26.7, 26.9, 27.4])
nx = len(x)
ny = len(y)
mx = np.mean(x)
my = np.mean(y)
sig2 = 1.7
u = (mx-my)/np.sqrt(sig2*(1/nx+1/ny))
pval = 2*(stats.norm.sf(abs(u)))
pval

0.04561646386460778

la p-val étant inférieure au seuil choisi (ici 0,05), on rejette H0

4. les deux forêts sont-elles toujours identiques si l’on suppose que la variance des hauteurs mesurées est inconnue ?
Justifiez votre raisonnement

In [8]:
#variance inconnue donc test de t-student

Sx = np.sum((x-mx)**2)
Sy = np.sum((y-my)**2)

shat = (Sx + Sy)/(nx+ny-2)

t = (mx-my)/np.sqrt(shat*(1/nx+1/ny))

pval = 2*(1 - stats.t.cdf(abs(t),nx+ny-2))

pval, shat, t

(0.10089874786736286, 2.341092307692308, 1.7033806219122543)

In [ ]:
# vérification à l'aide de scipy.stats
s,p = stats.ttest_ind(x,y)
print(s,p)

la p-val étant de 0.1 donc superieur à 0.05, on garde H0

## t-test pour la régression

D’aucuns prétendent que l’âge du capitaine d’un bateau est influencé par son nombre de voiles. Afin de vérifier cette hypothèse, les observations suivantes ont été rapportées :

Nom du bateau| L’aviso| Le Boutre| Côte à côte| Dinghy| Éole
---|---|---|---|---|---
Nombre de voiles| 2| 3| 5| 1| 8
Âge du capitaine| 25| 25| 20| 22| 16

1. La régression linéaire simple :     
    a. Posez un modèle de régression permettant d’expliquer l’âge du capitaine en fonction du nombre de voile d’un bateau.

$$
age = a * nombre + b + \varepsilon 
 $$

   b. Estimez les paramètres du modèle.

In [2]:
import numpy as np 
x = np.array([2, 3, 5, 1, 8])
y = np.array([25, 25, 20, 22, 16])
n = len(x)
X = np.stack([np.ones(n,), x], axis=1)
a = np.linalg.solve(X.T@X, X.T@y)
e = y - X@a
s2 = e.T@e/(n-2)
print(a)

[25.96753247 -1.14935065]


2. Peut-on raisonnablement affirmer que l’âge du capitaine dépend du nombre de voiles ?

a. Posez les hypothèses de votre test

H0 :  l’âge du capitaine ne dépend pas du nombre de voile : $a = 0$    
H1 :  l’âge du capitaine dépend du nombre de voile : $a \neq 0$

b. Calculez la p-valeur associée à vos observations

In [5]:
from scipy.stats import t
mx = np.mean(x)
s2x = (x-mx).T@(x-mx)
T = a[1]/np.sqrt(s2/s2x)
ddl = n-2
# par ce que T est négatif ! 
pval = t.cdf(T,ddl) + t.sf(-T, ddl)
print(pval)
print(T)

0.07262345584910318
-2.718790297950771


3. Quelles sont les hypothèses à faire sur le terme d’erreur dans le modèle de régression pour que l’utilisation du test de Student soit justifiée ?

les erreurs doivent être : 
 - normalement distribuées 
 - de même loi
 - indépendantes

4. Essayez de retrouver ces résultats à l'aide des packages scikitlearn et statsmodels
 - https://scikit-learn.org/stable/modules/linear_model.html#ordinary-least-squares

In [3]:
from sklearn import linear_model
Ma_Regression = linear_model.LinearRegression(fit_intercept=False)
Ma_Regression.fit(X,y)

LinearRegression(fit_intercept=False)

In [4]:
Ma_Regression.coef_, Ma_Regression.intercept_

(array([25.96753247, -1.14935065]), 0.0)

In [5]:
R2 = Ma_Regression.score(X,y)

In [6]:
SCT = np.sum((y-np.mean(y))**2)
SCR = (n-2)*s2
R2 = 1 - SCR/SCT
print(R2)

0.7113114158568705


## Rebelote

On s'intéresse au lien entre l'âge et la pression artérielle. Le tableau ci-dessous
donnent les pressions artérielles diastolique et systolique mesurées sur un échantillon de personnes
âgées de 17 à 73 ans.
On fera l'hypothèse que les pressions artérielle diastolique et systolique sont distribuées selon des lois normales dans la
population.
Dans la suite toutes les valeurs numériques proposées sont telles que les âges sont exprimés en
années et les pressions artérielles en mmHg.


Age| Pressoin Artérielle (diastolique) | Pressoin Artérielle (systolique)
--- | --- | ---
17 | 65 | 109
20 | 65 | 105
22 | 54 | 97
28 | 66 | 110
29 | 71 | 113
41 | 80 | 111
46 | 83 | 107
52 | 77 | 112
52 | 75 | 121
54 | 71 | 120
56 | 72 | 126
58 | 78 | 125
73 | 87 | 142


Est-ce que la différence entre la pression artérielle diastolique
et  la pression artérielle systolique augmente avec l'age ?



In [ ]:
data = np.array([[17 ,65 , 109],
[20 ,65 ,105],
[22 ,54 ,97],
[28 ,66 ,110],
[29 ,71 ,113],
[41 ,80 ,111],
[46 ,83 ,107],
[52 ,77 ,112],
[52 ,75 ,121],
[54 ,71 ,120],
[56 ,72 ,126],
[58 ,78 ,125],
[73 ,87 ,142]])
x = data[:,0]
y = data[:,2]-data[:,1]  # pour avoir des $y$ positifs

H0 :  la différence entre la pression artérielle diastolique et la pression artérielle systolique n'augmente pas avec l'age : $a = 0$    
H1 :  la différence entre la pression artérielle diastolique et la pression artérielle systolique augmente avec l'age : $a > 0$

In [ ]:
from scipy.stats import t
n = len(x)
X = np.stack([np.ones(n,), x], axis=1)
a = np.linalg.solve(X.T@X, X.T@y)
e = y - X@a
s2 = e.T@e/(n-2)
print(a, s2)

mx = np.mean(x)
s2x = (x-mx).T@(x-mx)
T = a[1]/np.sqrt(s2/s2x)
ddl = n-2
pval = (t.sf(T,ddl))
pval

on garde H0, la différence entre la pression artérielle diastolique
et  la pression artérielle systolique n'augmente pas avec l'age.

In [ ]:
model = sm.OLS(y, X).fit()
predictions = model.predict(X) # make the predictions by the model

# Print out the statistics
model.summary()

In [ ]:
print(y)